In [5]:
from tqdm.notebook import tqdm
import clip
import torch
device = "cuda" if torch.cuda.is_available() else "cpu"
print(device)

clip_model, clip_preprocess = clip.load("ViT-B/32", device)

cuda


In [6]:
from datasets import *
dataset_obj = Flowers102(0, 50)
train_loader, _ = dataset_obj.get_train_loaders(transform_fn=clip_preprocess)
test_loader = dataset_obj.get_test_loader(transform_fn=clip_preprocess)
classes = dataset_obj.classes

In [7]:
import copy

In [8]:
def get_clip_features(dataset):
    all_features = []
    all_labels = []

    global clip_model

    with torch.no_grad():
        for images, labels in tqdm(dataset):
            features = clip_model.encode_image(images.to(device))
            all_features.append(features)
            all_labels.append(labels)

    return torch.cat(all_features), torch.cat(all_labels)

train_features, train_labels = get_clip_features(train_loader)
test_features, test_labels = get_clip_features(test_loader)

  0%|          | 0/132 [00:00<?, ?it/s]

  0%|          | 0/17 [00:00<?, ?it/s]

In [9]:
def batch(iterable1,iterable2, n=1):
    l = len(iterable1)
    for ndx in range(0, l, n):
        yield (iterable1[ndx:min(ndx + n, l)], iterable2[ndx:min(ndx + n, l)])

out_train = batch(train_features,train_labels, 50)
out_test = batch(test_features,test_labels, 50)

In [10]:
import torch.nn as nn
import torch.optim as optim

class LogisticRegression(nn.Module):
    def __init__(self, input_dim, output_dim):
        super(LogisticRegression, self).__init__()
        self.linear = torch.nn.Linear(input_dim, output_dim)
        
    def forward(self, x):
        outputs = self.linear(x)
        return outputs
    
model = LogisticRegression(512,len(classes))
model.logit_scale = nn.Parameter(torch.ones([], device=device))
criterion = nn.CrossEntropyLoss()
learning_rate = 0.01
optimizer = torch.optim.SGD(model.parameters(), lr=learning_rate, weight_decay=1e-5)
num_epochs = 500
# scheduler = optim.lr_scheduler.MultiStepLR(
#             optimizer, milestones=[300, 500, 700, 900], gamma=0.1
#         )

In [11]:
def num_correct_preds(outputs, labels):
    _, predicted = outputs.max(1)
    return predicted.eq(labels).sum().item()

In [12]:
def cosine_loss(output, target):
    loss = 1 - torch.cosine_similarity(output, target)
    return loss

def calc_loss(outputs, labels, loss_name="ce"):
    
    loss_labels = labels
    
    criterion = nn.CrossEntropyLoss()

    if loss_name == "ce":
        return criterion(outputs, loss_labels) 

    elif loss_name == "dot":
        outputs = outputs / outputs.norm(dim=-1, keepdim=True)
        return -(outputs * loss_labels).sum(-1).mean()

    elif loss_name == "cosine":
        print(outputs.shape, loss_labels.shape)
        loss = torch.mean(cosine_loss(outputs, loss_labels))
        return loss

    elif loss_name == "temperature_ce":
        image_features = outputs

        # normalized features
        image_features = image_features / image_features.norm(dim=-1, keepdim=True)

        # cosine similarity as logits
        logit_scale = model.logit_scale.exp()
        logits_per_image = logit_scale * image_features @ text_features.t()
        return criterion(logits_per_image, labels)

In [13]:
# import torch
# from torch.utils.tensorboard import SummaryWriter
# writer = SummaryWriter()

In [15]:
import random

model.to(device)
model = model.to(torch.float16)

best_model = None
best_acc = -1

for epoch in tqdm(range(num_epochs+1)):
    
    model.train()
    running_loss = 0.0
    correct = 0.0
    total = 0

    if epoch%50 == 0:
        print("Shuffling")
        c = list(zip(train_features, train_labels))
        random.shuffle(c)
        train_features, train_labels = zip(*c)
        train_features = torch.stack(list(train_features))
        train_labels = torch.stack(list(train_labels))
        
    out_train = batch(train_features,train_labels, 50)
    for inputs, labels in out_train:
        
        inputs, labels = inputs.to(device), labels.to(device)
        
        optimizer.zero_grad()

        outputs = model(inputs)
        print(outputs, labels)
        loss = calc_loss(outputs, labels)

        loss.backward()

        optimizer.step()
        running_loss+=loss
        total += len(labels)
        correct += num_correct_preds(outputs, labels)
        
    if epoch%10 == 0:
        model.eval()
        out_test = batch(test_features,test_labels, 50)
        
        test_running_loss = 0.0
        test_correct = 0.0
        test_total = 0
        with torch.no_grad():
            for inputs, labels in tqdm(out_test):
        #         inputs = inputs / inputs.norm(dim=-1, keepdim=True)
                inputs, labels = inputs.to(device), labels.to(device)
                outputs = model(inputs)
                loss = criterion(outputs, labels)
                test_running_loss += loss.item()
                test_total += labels.size(0)
                test_correct += num_correct_preds(outputs, labels)

        epoch_loss = test_running_loss / len(test_loader)
#         writer.add_scalar("Loss/val", epoch_loss, epoch)
        epoch_accuracy = test_correct * 100 / test_total
#         writer.add_scalar("Accuracy/val", epoch_loss, epoch)
        if epoch_accuracy > best_acc:
            best_model= copy.deepcopy(model)
            best_acc = epoch_accuracy
            print("Found best model")
#         print(
#             f"Testing: Epoch {epoch} || Loss: {epoch_loss:7.3f} || Accuracy: {epoch_accuracy:6.2f}%"
#         )

        
    epoch_loss = running_loss/len(train_loader)
#     writer.add_scalar("Loss/train", epoch_loss, epoch)
    epoch_accuracy = correct*100/total
#     writer.add_scalar("Accuracy/train", epoch_loss, epoch)
    print(
        f"Training: Epoch {epoch} || Loss: {epoch_loss:7.3f} || Accuracy: {epoch_accuracy:6.2f}%"
    )

#     writer.flush()
# writer.close()


  0%|          | 0/501 [00:00<?, ?it/s]

Shuffling
tensor([[-0.3679, -0.0978, -0.5479,  ..., -0.2454,  0.3862, -0.0397],
        [-0.4412, -0.2700, -0.3984,  ..., -0.2888,  0.0526, -0.1776],
        [-0.4080, -0.4868, -0.3340,  ..., -0.2244, -0.1191,  0.0240],
        ...,
        [-0.4497, -0.2360, -0.6748,  ..., -0.1409, -0.0643, -0.1108],
        [-0.3154, -0.4355, -0.4141,  ..., -0.0940, -0.1173, -0.1974],
        [-0.4275, -0.2484, -0.2269,  ..., -0.1661,  0.1283, -0.2239]],
       device='cuda:0', dtype=torch.float16, grad_fn=<AddmmBackward>) tensor([ 94,  84,  45,  81,  28,  85,  57,  77,  98,  11,  27,  55,  14,  99,
         84,  13,  11,  67,  89,  26,  52,   1, 101,  91,  41,  33,  27,  77,
         77,  84,  98,  23,  78,  10,  84,  35,  82,  84,  80,  51,  93,  41,
         54,  96,  82,  52,  53,  17,  49,  92], device='cuda:0')
tensor([[-0.4355, -0.1898, -0.4900,  ..., -0.1119,  0.0995,  0.1312],
        [-0.4509, -0.5264, -0.2952,  ...,  0.0543, -0.1660,  0.0556],
        [-0.7319, -0.4072, -0.5239,  ..., -0.3

tensor([[-0.4373, -0.3540, -0.5483,  ..., -0.1451, -0.2379, -0.2269],
        [-0.4099, -0.2698, -0.2001,  ..., -0.3721, -0.2338, -0.3911],
        [-0.4871, -0.4941, -0.3914,  ..., -0.1663, -0.0020, -0.0408],
        ...,
        [-0.3879, -0.5239, -0.3579,  ..., -0.1328, -0.2047, -0.1450],
        [-0.5493, -0.3093, -0.4033,  ..., -0.2477,  0.1893,  0.0130],
        [-0.5942, -0.6270, -0.4426,  ..., -0.2157,  0.1630,  0.0097]],
       device='cuda:0', dtype=torch.float16, grad_fn=<AddmmBackward>) tensor([ 93,   9,  86,  32,  54,  77,  94,  84,  64,  73,  23,  96,  18,  55,
         11,  72,  32,  87,  87,  15,  83,  40,  72,   5,  37,  33,  72,  61,
         40,  77,   5,  41,  83,  79,   5, 100,  49,  91,  26,  77,  57,  49,
         44,  56,  21,  19,  74,  51,   8,  82], device='cuda:0')
tensor([[-0.6655, -0.6221, -0.5337,  ..., -0.1152,  0.0575, -0.4243],
        [-0.4248, -0.1993, -0.5283,  ..., -0.2274, -0.1708, -0.0638],
        [-0.6372, -0.2812, -0.0993,  ..., -0.1088,  0.03

tensor([[-0.5449, -0.1512, -0.3894,  ..., -0.1322,  0.0071,  0.2236],
        [-0.7153, -0.2993, -0.0610,  ..., -0.1519,  0.2288, -0.1819],
        [-0.5986, -0.6348, -0.4434,  ..., -0.0690,  0.5205, -0.1725],
        ...,
        [-0.6797, -0.1755, -0.3716,  ..., -0.3562,  0.1998, -0.0981],
        [-0.6802, -0.4692, -0.5190,  ..., -0.2000, -0.2249, -0.1918],
        [-0.8755, -0.4890, -0.5347,  ..., -0.0594,  0.1694, -0.3596]],
       device='cuda:0', dtype=torch.float16, grad_fn=<AddmmBackward>) tensor([ 77,  48,  95,  80,  96,  42,  36,  85,  60,  49,  26,  80,  45,  68,
         57,  85,  75,  22,  42,  27,  73,  87,  56,  84,  96,  77,  43,  57,
         85,  51,  32, 101,   5,  11,  56,  96,  92,  36,  75,  64,  74,  35,
         17,  89,  33,  82,  11,  62,  68,  55], device='cuda:0')
tensor([[-0.5327, -0.5151, -0.5254,  ..., -0.1924,  0.1123, -0.1154],
        [-0.6406, -0.7085, -0.5225,  ..., -0.1633,  0.3484, -0.1145],
        [-0.5615, -0.5107, -0.4443,  ..., -0.1648, -0.16

0it [00:00, ?it/s]

...

tensor([[ 0.1665,  2.0293,  0.6021,  ...,  0.8921, -0.3367, -0.6929],
        [-0.3010, -0.5815,  0.4307,  ...,  0.2515,  0.8740, -0.3599],
        [-0.3298,  1.0420,  0.6997,  ...,  0.0389,  0.6982,  0.7817],
        ...,
        [-0.4773, -1.0361,  0.0920,  ...,  0.4578, -0.1443,  1.1650],
        [ 1.0586, -0.3040,  0.5273,  ...,  0.4595,  1.1768, -1.2930],
        [-0.4451, -1.1934, -0.7192,  ...,  1.6748,  0.5527,  1.5625]],
       device='cuda:0', dtype=torch.float16, grad_fn=<AddmmBackward>) tensor([34, 43, 29, 14, 23, 11, 48, 49, 30, 75, 82, 98, 82, 57, 90,  9, 80, 33,
        81, 66, 33, 71, 21, 49, 91,  3, 79, 26, 86, 23, 89, 71, 98, 42, 26, 84,
        49, 25, 52, 73, 54, 74, 43, 53, 97, 91, 99,  4, 50, 81],
       device='cuda:0')
tensor([[ 0.2131, -0.4004, -0.2375,  ...,  3.9297,  0.2050, -0.0133],
        [ 0.4314, -1.0547, -0.2432,  ..., -0.0235,  1.5352, -0.6528],
        [-0.6255,  0.0710, -0.3757,  ...,  0.5381,  0.9365,  2.1406],
        ...,
        [ 0.3245,  1.625

tensor([[ 1.5015e-01, -1.4492e+00, -4.3066e-01,  ...,  1.5957e+00,
          1.7354e+00,  8.0273e-01],
        [ 1.9629e-01, -1.0654e+00, -4.6509e-01,  ...,  1.3740e+00,
          5.4413e-02, -4.3506e-01],
        [-4.4507e-01, -1.2686e+00, -4.9686e-04,  ...,  1.7451e+00,
          5.1416e-01,  1.0078e+00],
        ...,
        [ 2.4719e-01,  3.7354e-02, -4.8486e-01,  ...,  6.2744e-01,
          4.2310e-01, -2.6343e-01],
        [-2.8296e-01,  1.2676e+00,  1.6621e+00,  ...,  2.1469e-02,
         -5.8057e-01,  2.8223e-01],
        [-8.1970e-02,  5.3955e-01,  9.5996e-01,  ...,  8.1152e-01,
          1.1846e+00,  5.8563e-02]], device='cuda:0', dtype=torch.float16,
       grad_fn=<AddmmBackward>) tensor([84, 56, 81, 22, 59, 80, 73, 73, 11, 81, 63, 59,  7, 91, 49, 18, 96, 62,
        44, 86, 65, 82, 58, 38, 97, 53, 74, 38, 50, 51, 42, 44, 22, 82, 80, 99,
        32, 49,  9, 27, 63, 50, 68, 49, 86, 93, 73, 89, 48, 44],
       device='cuda:0')
tensor([[-4.4327e-03, -5.3467e-01, -1.5356e-01,  

tensor([[ 0.6372,  2.4512,  0.6025,  ...,  0.1429,  1.5664,  0.1305],
        [-0.3457,  0.5288,  0.6436,  ...,  1.3818,  0.3330,  1.7061],
        [ 0.3320, -0.9683, -0.3728,  ...,  0.4167,  1.2803,  0.2661],
        ...,
        [-0.0304, -0.8149,  0.4570,  ...,  0.0048,  0.3008, -0.1832],
        [ 0.5928, -0.4138, -0.6904,  ...,  1.2021,  1.5361, -1.3730],
        [-0.2847, -1.2520, -0.6108,  ...,  1.3711,  0.7036,  0.7793]],
       device='cuda:0', dtype=torch.float16, grad_fn=<AddmmBackward>) tensor([29, 77, 72, 47, 93, 47, 89, 84,  5, 18, 29,  1,  2, 26, 89, 84, 77,  6,
        49, 44, 44, 32, 14, 77, 49, 88, 46, 90, 59, 22, 56, 49, 24, 41, 51, 94,
        32, 61, 34, 77, 28, 88, 74, 80, 19, 76, 50, 43, 49, 36],
       device='cuda:0')
tensor([[ 0.6196, -0.0399, -0.0342,  ...,  0.1350,  4.0586, -0.5210],
        [ 1.4268, -1.1855,  0.0704,  ...,  1.4629,  1.4170, -1.1445],
        [ 0.6982, -0.5010, -0.7905,  ...,  0.7446,  0.5303, -0.8286],
        ...,
        [-0.1863, -0.913

tensor([[ 0.3589, -1.2539, -0.1708,  ...,  0.4653,  1.6533,  0.9424],
        [ 0.7817, -0.0513,  0.6646,  ...,  1.3447,  1.8066, -0.4270],
        [ 0.1144,  1.8838,  0.7749,  ..., -0.1760,  0.2524,  0.5923],
        ...,
        [ 0.6177, -0.7749, -0.4919,  ...,  0.8560,  2.6035,  0.2598],
        [ 0.2089, -0.3596, -1.0840,  ...,  1.1094,  1.3076, -0.3584],
        [ 0.7690, -1.4219, -0.1147,  ...,  2.1934,  1.5713, -0.5566]],
       device='cuda:0', dtype=torch.float16, grad_fn=<AddmmBackward>) tensor([72, 49, 29, 87, 32, 48, 71, 31,  6, 81, 74, 56, 43, 48, 74, 48, 97, 51,
        82, 73, 32,  6, 55, 14, 81, 66, 97, 60, 90, 54, 76, 57, 12, 37, 22, 45,
        40, 59, 97, 19, 82, 54, 49, 42, 37, 67, 43, 72, 75, 90],
       device='cuda:0')
tensor([[ 0.6143,  1.8301,  0.7163,  ..., -0.4153,  0.5449, -0.7480],
        [-0.3611,  0.3745,  3.3770,  ..., -0.3892, -1.2461,  0.9619],
        [-0.2491, -0.4197,  0.5601,  ...,  0.4526,  0.3892, -1.0010],
        ...,
        [-1.0039, -1.222

KeyboardInterrupt: 

In [30]:
embeddings = torch.from_numpy(best_model.linear.weight.detach().cpu().numpy()).to(torch.float16)

In [31]:
zeroshot_weights = torch.from_numpy(np.array(embeddings).T).to(torch.float16)

def accuracy(output, target, topk=(1,)):
    pred = output.topk(max(topk), 1, True, True)[1].t()
    correct = pred.eq(target.view(1, -1).expand_as(pred))
    return [
        float(correct[:k].reshape(-1).float().sum(0, keepdim=True).cpu().numpy())
        for k in topk
    ]

# lazy load
if clip_model == None:
    clip_model, clip_preprocess = clip.load(clip_model_name, device)

with torch.no_grad():
    top1, top5, n = 0.0, 0.0, 0.0
    for i, (images, target) in enumerate(tqdm(test_loader)):
        images = images.cuda()
        target = target.cuda()

        # predict

        image_features = clip_model.encode_image(images)
        image_features /= image_features.norm(dim=-1, keepdim=True)
        logits = 100.0 * image_features.to(device) @ zeroshot_weights.to(device)

        # measure accuracy
        acc1, _ = accuracy(logits, target, topk=(1, 5))
        top1 += acc1
        n += images.size(0)

top1 = (top1 / n) * 100

print("acc:", top1)

  0%|          | 0/303 [00:00<?, ?it/s]

acc: 82.69966996699671


## Deterministic - (using sci-kit)

In [32]:
global clip_model, clip_preprocess
from sklearn.linear_model import LogisticRegression

len_classes = len(classes)

train_features, train_labels = get_clip_features(train_loader)
test_features, test_labels = get_clip_features(test_loader)

train_features = train_features / train_features.norm(dim=-1, keepdim=True)
test_features = test_features / test_features.norm(dim=-1, keepdim=True)

classifier = LogisticRegression(C=1, max_iter=1000, n_jobs=4,verbose=1)
classifier.fit(train_features.cpu().numpy(), train_labels.cpu().numpy())
predictions = classifier.predict(test_features.cpu().numpy())
accuracy = np.mean((test_labels.cpu().numpy() == predictions).astype(np.float)) * 100.0

print(accuracy)

  0%|          | 0/1515 [00:00<?, ?it/s]

  0%|          | 0/303 [00:00<?, ?it/s]

[Parallel(n_jobs=4)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done   1 out of   1 | elapsed:  2.1min finished


83.86138613861385
